In [2]:
import pandas as pd
import os
from collections import defaultdict
import paramiko # for ssh
import traceback #  for error handling
import plotly.express as px
        

c:\Users\liyoa\anaconda3\Lib\site-packages\paramiko\transport.py:219: CryptographyDeprecationWarning: Blowfish has been deprecated
  "class": algorithms.Blowfish,


In [3]:
cgc_data = pd.read_csv('Census_allTue Apr  9 04_58_38 2024.csv')
cgc_data.head()

Gene Symbol                                               Name  \
0        A1CF                     APOBEC1 complementation factor   
1        ABI1                                   abl-interactor 1   
2        ABL1  v-abl Abelson murine leukemia viral oncogene h...   
3        ABL2     c-abl oncogene 2, non-receptor tyrosine kinase   
4       ACKR3                      atypical chemokine receptor 3   

   Entrez GeneId        Genome Location  Tier Hallmark  Chr Band Somatic  \
0        29974.0   10:50799421-50885675     2      NaN  10q11.23     yes   
1        10006.0   10:26746593-26860935     1      Yes   10p12.1     yes   
2           25.0  9:130713946-130885683     1      Yes   9q34.12     yes   
3           27.0  1:179099327-179229601     1      NaN    1q25.2     yes   
4        57007.0  2:236569641-236582358     1      Yes    2q37.3     yes   

  Germline Tumour Types(Somatic) Tumour Types(Germline) Cancer Syndrome  \
0      NaN              melanoma                    NaN             NaN   
1      NaN                   AML                    NaN             NaN   
2      NaN       CML, ALL, T-ALL                    NaN             NaN   
3      NaN                   AML                    NaN             NaN   
4      NaN                lipoma                    NaN             NaN   

  Tissue Type Molecular Genetics    Role in Cancer Mutation Types  \
0           E                NaN          oncogene            Mis   
1           L                Dom       TSG, fusion              T   
2           L                Dom  oncogene, fusion         T, Mis   
3           L                Dom  oncogene, fusion              T   
4           M                Dom  oncogene, fusion              T   

  Translocation Partner Other Germline Mut Other Syndrome  \
0                   NaN                NaN            NaN   
1                 KMT2A                NaN            NaN   
2     BCR, ETV6, NUP214                NaN            NaN   
3                  ETV6                NaN            NaN   
4                 HMGA2                NaN            NaN   

                                            Synonyms  
0  ACF,ACF64,ACF65,APOBEC1CF,ASP,CCDS73133.1,ENSG...  
1  ABI-1,CCDS7150.1,E3B1,ENSG00000136754.17,NM_00...  
2  ABL,CCDS35165.1,ENSG00000097007.17,JTK7,NM_007...  
3  ABLL,ARG,CCDS30947.1,ENSG00000143322.19,NM_007...  
4  CCDS2516.1,CMKOR1,CXCR7,ENSG00000144476.5,GPR1...

In [3]:
cgc_data.loc[307, :]

Gene Symbol                                                        HMGN2P46
Name                      high mobility group nucleosomal binding domain...
Entrez GeneId                                                           NaN
Genome Location                                        15:45511136-45556730
Tier                                                                      2
Hallmark                                                                NaN
Chr Band                                                            15q21.1
Somatic                                                                 yes
Germline                                                                NaN
Tumour Types(Somatic)                                              prostate
Tumour Types(Germline)                                                  NaN
Cancer Syndrome                                                         NaN
Tissue Type                                                               E
Molecular Ge

In [17]:
import requests

def get_pdb_ids(gene_symbol, entrez_gene_id, synonyms):
    api_url = f"http://mygene.info/v3/query?q={gene_symbol}&species=human&fields=entrezgene,ensembl,pdb"
    response = requests.get(api_url)
    # check response
    if response.status_code != 200:
        return response.status_code, None
    response = response.json()
    for hit in response['hits']:
        if ( str(hit['_id']) == str(int(entrez_gene_id)) ) or ( synonyms and 'ensembl' in hit and hit['ensembl']['gene'] in synonyms ): # (sometimes entrez_gene_id might not match but ensembl gene does
            if 'pdb' in hit:
                return 200, hit['pdb'] # status_code, pdb_ids
            else: # no structures found 
                continue
    return 200, None


In [18]:
# add pdb structures to cgc_data
pdb_structures = []
count = 1
for _, row in cgc_data.iterrows():
    # print curent count, replace previous line    
    gene_symbol = row['Gene Symbol']
    entrez_gene_id = row['Entrez GeneId']
    synonyms = row['Synonyms']
    print(f"Processing {count} of {len(cgc_data)} ({gene_symbol})", end='\r')
    count += 1

    try:
        status, pdb = get_pdb_ids(gene_symbol, entrez_gene_id, synonyms)
    except Exception as e:
        print(f"Failed to get pdb ids for {gene_symbol} with error {e}")
        pdb_structures.append(None)
        continue

    if not pdb:
        print(f"Failed to get pdb ids for {gene_symbol} with status code {status}")
        pdb_structures.append(None)
    else:
        pdb_structures.append(list(pdb))

cgc_data['PDB Structures'] = pdb_structures

Failed to get pdb ids for ACSL3 with status code 200
Failed to get pdb ids for ACSL6 with status code 200
Failed to get pdb ids for AFF3 with status code 200
Failed to get pdb ids for AKAP9 with status code 200
Failed to get pdb ids for ARHGEF10 with status code 200
Failed to get pdb ids for ARHGEF10L with status code 200
Failed to get pdb ids for ASPM with status code 200


KeyboardInterrupt: 

In [ ]:
cgc_data.head(3)

Gene Symbol                                               Name  \
0        A1CF                     APOBEC1 complementation factor   
1        ABI1                                   abl-interactor 1   
2        ABL1  v-abl Abelson murine leukemia viral oncogene h...   

   Entrez GeneId        Genome Location  Tier Hallmark  Chr Band Somatic  \
0        29974.0   10:50799421-50885675     2      NaN  10q11.23     yes   
1        10006.0   10:26746593-26860935     1      Yes   10p12.1     yes   
2           25.0  9:130713946-130885683     1      Yes   9q34.12     yes   

  Germline Tumour Types(Somatic)  ... Cancer Syndrome Tissue Type  \
0      NaN              melanoma  ...             NaN           E   
1      NaN                   AML  ...             NaN           L   
2      NaN       CML, ALL, T-ALL  ...             NaN           L   

  Molecular Genetics    Role in Cancer Mutation Types Translocation Partner  \
0                NaN          oncogene            Mis                   NaN   
1                Dom       TSG, fusion              T                 KMT2A   
2                Dom  oncogene, fusion         T, Mis     BCR, ETV6, NUP214   

  Other Germline Mut Other Syndrome  \
0                NaN            NaN   
1                NaN            NaN   
2                NaN            NaN   

                                            Synonyms  \
0  ACF,ACF64,ACF65,APOBEC1CF,ASP,CCDS73133.1,ENSG...   
1  ABI-1,CCDS7150.1,E3B1,ENSG00000136754.17,NM_00...   
2  ABL,CCDS35165.1,ENSG00000097007.17,JTK7,NM_007...   

                                      PDB Structures  
0                                               2CPD  
1                                               7LXE  
2  [1AB2, 1AWO, 1BBZ, 1JU5, 1OPL, 1ZZP, 2ABL, 2E2...  

[3 rows x 21 columns]

In [14]:
def dwl_pdb_file(pdb_id):
    base_url = 'https://files.rcsb.org/download/'
    pdb_url = base_url + pdb_id + '.pdb'
    response = requests.get(pdb_url)
    # Check if the request was successful
    if response.status_code == 200:
        # Save the PDB file to pdb_files folder
        with open(f'pdb_files/{pdb_id}.pdb', 'wb') as f:
            f.write(response.content)
    else:
        print(f"Failed to download PDB file {pdb_id}. Status code:", response.status_code)
    return


In [15]:
def get_resolution(pdb_id):
    try:
        with open(f'pdb_files/{pdb_id}.pdb', 'r') as f:
            pdb_text = f.read()

            # find line REMARK   2 RESOLUTION.
            resolution = None
            for line in pdb_text.split('\n'):
                if line.startswith('REMARK   2 RESOLUTION.'):
                    resolution = line.split("REMARK   2 RESOLUTION.")[1].strip()
                    break
        if "ANGSTROM" in resolution:
            resolution = resolution.replace(" ANGSTROMS.", "").strip()
        else:
            # print(f"Resolution not found for {pdb_id}")
            resolution = None
    except Exception as e:
        print(f"Failed to get resolution for {pdb_id} with error {e}")
        resolution = None
    return resolution

In [ ]:
# count number of elements in each pdb_structure
lens = []
for i in pdb_structures:
    # if value is list
    if isinstance(i, list):
        lens.append(len(i))
    elif i is not None:
        lens.append(1)
    else:
        lens.append(0)

cgc_data['n_structures'] = lens
cgc_data.head(3)

Gene Symbol                                               Name  \
0        A1CF                     APOBEC1 complementation factor   
1        ABI1                                   abl-interactor 1   
2        ABL1  v-abl Abelson murine leukemia viral oncogene h...   

   Entrez GeneId        Genome Location  Tier Hallmark  Chr Band Somatic  \
0        29974.0   10:50799421-50885675     2      NaN  10q11.23     yes   
1        10006.0   10:26746593-26860935     1      Yes   10p12.1     yes   
2           25.0  9:130713946-130885683     1      Yes   9q34.12     yes   

  Germline Tumour Types(Somatic)  ... Tissue Type Molecular Genetics  \
0      NaN              melanoma  ...           E                NaN   
1      NaN                   AML  ...           L                Dom   
2      NaN       CML, ALL, T-ALL  ...           L                Dom   

     Role in Cancer Mutation Types Translocation Partner Other Germline Mut  \
0          oncogene            Mis                   NaN                NaN   
1       TSG, fusion              T                 KMT2A                NaN   
2  oncogene, fusion         T, Mis     BCR, ETV6, NUP214                NaN   

  Other Syndrome                                           Synonyms  \
0            NaN  ACF,ACF64,ACF65,APOBEC1CF,ASP,CCDS73133.1,ENSG...   
1            NaN  ABI-1,CCDS7150.1,E3B1,ENSG00000136754.17,NM_00...   
2            NaN  ABL,CCDS35165.1,ENSG00000097007.17,JTK7,NM_007...   

                                      PDB Structures n_structures  
0                                               2CPD            1  
1                                               7LXE            1  
2  [1AB2, 1AWO, 1BBZ, 1JU5, 1OPL, 1ZZP, 2ABL, 2E2...           81  

[3 rows x 22 columns]

In [19]:
# download pdb files
tmp_genes = ["KRAS", "EGFR", "TP53", "HRAS"]
resolutions = defaultdict(dict)

# count number of structures for all gene
n_total = cgc_data[cgc_data['Gene Symbol'].isin(tmp_genes)]["n_structures"].sum()

for gene in tmp_genes:
    pdb_structures = cgc_data[cgc_data['Gene Symbol'] == gene]['PDB Structures'].values[0]
    if pdb_structures:
        for pdb_id in pdb_structures:
            n_total -= 1
            print(f"Downloading PDB file {pdb_id} for {gene} ({n_total} structures remaining)", end='\r')
            # check if the file already exists
            if not os.path.exists(f'pdb_files/{pdb_id}.pdb'):
                dwl_pdb_file(pdb_id)
            resolution = get_resolution(pdb_id)
            resolutions[gene][pdb_id] = resolution
        

In [20]:
def sort_pdb_ids_by_resolution(gene_id):
    pdb_resolutions = resolutions[gene_id]
    sorted_pdb_ids = sorted(pdb_resolutions, key=lambda pdb_id: float('inf') if pdb_resolutions[pdb_id] is None else float(pdb_resolutions[pdb_id]))
    sorted_resolutions = [(pdb_id, pdb_resolutions[pdb_id]) for pdb_id in sorted_pdb_ids]
    return sorted_resolutions

top_structures = dict()
n = 30
for gene_id in resolutions:
    sorted_pdb_resolutions = sort_pdb_ids_by_resolution(gene_id)
    print(f"\nTop {n} structures for Gene {gene_id}:")
    for pdb_id, resolution in sorted_pdb_resolutions[:n]:
        print(f"PDB ID: {pdb_id}, Resolution: {resolution}")
    top_structures[gene_id] = [i[0] for i in sorted_pdb_resolutions[:n]]

In [3]:
top_structures = {'KRAS': ['6P0Z',
  '8ONV',
  '8AZZ',
  '4QL3',
  '8AZX',
  '8B00',
  '8AZV',
  '8AZY',
  '8B78',
  '8AFB'],
 'EGFR': ['8A27',
  '8A2D',
  '5UG9',
  '5HG8',
  '8A2A',
  '5UG8',
  '3POZ',
  '6TFV',
  '6TG0',
  '3VRP'],
 'TP53': ['3D06',
  '5MHC',
  '6GGC',
  '6SHZ',
  '4MZI',
  '6GGE',
  '3LW1',
  '5O1E',
  '6RL3',
  '8E7A'],
 'HRAS': ['2CE2',
  '2EVW',
  '2CLD',
  '2CL6',
  '2CL7',
  '5WDQ',
  '1CTQ',
  '2CLC',
  '3K8Y',
  '3OIW']}
# top_structures

In [4]:
from stat import S_ISDIR

In [5]:
def download_directory(sftp, remote_dir, local_dir):
    for item in sftp.listdir_attr(remote_dir):
        remote_path = remote_dir + '/' + item.filename
        local_path = os.path.join(local_dir, item.filename)
        if S_ISDIR(item.st_mode):
            os.makedirs(local_path, exist_ok=True)
            download_directory(sftp, remote_path, local_path)
        else:
            sftp.get(remote_path, local_path)

In [6]:
# get all chains in pdb file
def get_chains_pdb_id(pdb_id):
    with open(f'pdb_files/{pdb_id}.pdb', 'r') as f:
        pdb_text = f.read()
        chains = []
        for line in pdb_text.split('\n'):
            if line.startswith('DBREF'):
                chain = line.split()[2]
                chains.append(chain)
    return chains

get_chains_pdb_id('6SHZ')

['A', 'B']

In [23]:
host = "m3-dtn.massive.org.au"
username = "yliy0004"
with open("pw.txt", "r") as f:
    password = f.read()
base_path = 'ym65_scratch/yliy0004/NetworkAnalysis'

client = paramiko.client.SSHClient()
client.set_missing_host_key_policy(paramiko.AutoAddPolicy())
client.connect(host, username=username, password=password)

# check if R module is loaded (uses .bashrc - not the best solution because STRUDEL cannot be used, make sure to correct this if using STRUDEL)
stdin,stdout,stderr=client.exec_command('R --version') 
print(stdout.read().decode())
print(stderr.read().decode())

sftp_client=client.open_sftp()

# ==================== SBNA ====================

prev_id = None # used to delete the previous directory
for gene_id in top_structures:
    for pdb_id in top_structures[gene_id]:

        # remove all previous results
        if prev_id:
            try:
                client.exec_command(f"rm -rf {base_path}/{prev_id}")
            except:
                pass
        prev_id = pdb_id

        # get available chains
        try:
            chains = get_chains_pdb_id(pdb_id)
        except Exception as e:
            print(f"Failed to get chains for {pdb_id} with error {e}")
            continue
        
        for chain in chains: 
            local_dir = f"sbna_results/{pdb_id}/{chain}"
            if os.path.exists(f"{local_dir}/{pdb_id}_monomer/FinalSum"): # skip if analysis already done and downloaded
                continue
            try:
                print(f"\nProcessing {pdb_id}...")
                sftp_client.mkdir(f'{base_path}/{pdb_id}') # will be error if directory already exists
                sftp_client.put(f"pdb_files/{pdb_id}.pdb", f'{base_path}/{pdb_id}/{pdb_id}.pdb') # upload pdb file to the remote directory
                client.exec_command(f"cp {base_path}/sbna.sh {base_path}/{pdb_id}/sbna.sh") # copy the sbna.sh file to the subdirectory
                stdin,stdout,stderr=client.exec_command(f'cd {base_path}/{pdb_id}; sh sbna.sh {pdb_id}.pdb "Chain {chain}"') # run the sbna.sh script
                print(stdout.read().decode())
                # check if Final_sum file exists
                print(stderr.read().decode('utf-8'))
                stdin,stdout,stderr=client.exec_command(f"ls {base_path}/{pdb_id}/{pdb_id}_monomer/FinalSum")
                # print error message if no output

                # download the sbna results
                if not stdout.read().decode():
                    print(f"Final_sum file not found for {pdb_id}")
                    continue
                
                # download the pdb_id directory
                os.makedirs(local_dir, exist_ok=True) # create the directory if it doesn't exist
                download_directory(sftp_client, f"{base_path}/{pdb_id}", local_dir)
                print(f"SBNA results for {pdb_id} succesfully downloaded")
            except Exception:
                # print full error message
                print(f"Failed to process {pdb_id} with error:")
                print(traceback.print_exc())
                continue

if prev_id:
    try:
        client.exec_command(f"rm -rf {base_path}/{prev_id}")
    except:
        pass


client.close()
sftp_client.close()

R version 4.0.5 (2021-03-31) -- "Shake and Throw"
Copyright (C) 2021 The R Foundation for Statistical Computing
Platform: x86_64-pc-linux-gnu (64-bit)

R is free software and comes with ABSOLUTELY NO WARRANTY.
You are welcome to redistribute it under the terms of the
GNU General Public License versions 2 or 3.
For more information about these matters see
https://www.gnu.org/licenses/.




Processing 6P0Z...


Final_sum file not found for 6P0Z


Secsh channel 14 open FAILED: open failed: Administratively prohibited



Processing 6TFV...
Starting phenix.pdbtools
on Mon Apr 15 18:35:43 2024 by yliy0004

Processing files:
-------------------------------------------------------------------------------

  Found model, 6TFV.pdb

Processing PHIL parameters:
-------------------------------------------------------------------------------

  Adding command-line PHIL:
  -------------------------
    keep=Chain B

Final processed PHIL parameters:
-------------------------------------------------------------------------------
  data_manager {
    model {
      file = "6TFV.pdb"
    }
    default_model = "6TFV.pdb"
  }
  modify {
    keep = Chain B
  }


Starting job
Validating inputs
Performing manipulations
Size before: 4667 size after: 2274
Writing output model

Job complete
usr+sys time: 2.03 seconds
wall clock time: 2.56 seconds
Cleaning PDB file
Starting phenix.pdbtools
on Mon Apr 15 18:35:46 2024 by yliy0004

Processing files:
-------------------------------------------------------------------------------

Traceback (most recent call last):
  File "C:\Users\liyoa\AppData\Local\Temp\ipykernel_20644\3788805321.py", line 44, in <module>
    sftp_client.mkdir(f'{base_path}/{pdb_id}') # will be error if directory already exists
    ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\liyoa\anaconda3\Lib\site-packages\paramiko\sftp_client.py", line 460, in mkdir
    self._request(CMD_MKDIR, path, attr)
  File "c:\Users\liyoa\anaconda3\Lib\site-packages\paramiko\sftp_client.py", line 822, in _request
    return self._read_response(num)
           ^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\liyoa\anaconda3\Lib\site-packages\paramiko\sftp_client.py", line 874, in _read_response
    self._convert_status(msg)
  File "c:\Users\liyoa\anaconda3\Lib\site-packages\paramiko\sftp_client.py", line 907, in _convert_status
    raise IOError(text)
OSError: Failure


Starting phenix.pdbtools
on Mon Apr 15 18:49:58 2024 by yliy0004

Processing files:
-------------------------------------------------------------------------------

  Found model, 5MHC.pdb

Processing PHIL parameters:
-------------------------------------------------------------------------------

  Adding command-line PHIL:
  -------------------------
    keep=Chain P

Final processed PHIL parameters:
-------------------------------------------------------------------------------
  data_manager {
    model {
      file = "5MHC.pdb"
    }
    default_model = "5MHC.pdb"
  }
  modify {
    keep = Chain P
  }


Starting job
Validating inputs
Performing manipulations
Size before: 4775 size after: 203
Writing output model

Job complete
usr+sys time: 1.91 seconds
wall clock time: 1.92 seconds
Cleaning PDB file
Starting phenix.pdbtools
on Mon Apr 15 18:50:01 2024 by yliy0004

Processing files:
-------------------------------------------------------------------------------

  Found model, 5MHC

In [12]:
host = "m3-dtn.massive.org.au"
username = "yliy0004"
with open("pw.txt", "r") as f:
    password = f.read()
base_path = 'ym65_scratch/yliy0004/NetworkAnalysis'

client = paramiko.client.SSHClient()
client.set_missing_host_key_policy(paramiko.AutoAddPolicy())
client.connect(host, username=username, password=password)

# check if R module is loaded (uses .bashrc - not the best solution because STRUDEL cannot be used, make sure to correct this if using STRUDEL)
stdin,stdout,stderr=client.exec_command('R --version') 
print(stdout.read().decode())
print(stderr.read().decode())

sftp_client=client.open_sftp()

# ==================== SBNA ====================

prev_id = None # used to delete the previous directory
# for gene_id in top_structures:
for pdb_id in ['6SHZ']:

    # remove all previous results
    if prev_id:
        try:
            client.exec_command(f"rm -rf {base_path}/{prev_id}")
        except:
            pass
    prev_id = pdb_id

    # get available chains
    try:
        chains = get_chains_pdb_id(pdb_id)
    except Exception as e:
        print(f"Failed to get chains for {pdb_id} with error {e}")
        continue
    
    for chain in chains: 
        local_dir = f"sbna_results/{pdb_id}/{chain}"
        if os.path.exists(f"{local_dir}/{pdb_id}_monomer/FinalSum"): # skip if analysis already done and downloaded
            continue
        try:
            print(f"\nProcessing {pdb_id}...")
            sftp_client.mkdir(f'{base_path}/{pdb_id}') # will be error if directory already exists
            sftp_client.put(f"pdb_files/{pdb_id}.pdb", f'{base_path}/{pdb_id}/{pdb_id}.pdb') # upload pdb file to the remote directory
            client.exec_command(f"cp {base_path}/sbna.sh {base_path}/{pdb_id}/sbna.sh") # copy the sbna.sh file to the subdirectory
            stdin,stdout,stderr=client.exec_command(f'cd {base_path}/{pdb_id}; sh sbna.sh {pdb_id}.pdb "Chain {chain}"') # run the sbna.sh script
            print(stdout.read().decode())
            # check if Final_sum file exists
            print(stderr.read().decode('utf-8'))
            stdin,stdout,stderr=client.exec_command(f"ls {base_path}/{pdb_id}/{pdb_id}_monomer/FinalSum")
            # print error message if no output

            # download the sbna results
            if not stdout.read().decode():
                print(f"Final_sum file not found for {pdb_id}")
                continue
            
            # download the pdb_id directory
            os.makedirs(local_dir, exist_ok=True) # create the directory if it doesn't exist
            download_directory(sftp_client, f"{base_path}/{pdb_id}", local_dir)
            print(f"SBNA results for {pdb_id} succesfully downloaded")
        except Exception:
            # print full error message
            print(f"Failed to process {pdb_id} with error:")
            print(traceback.print_exc())
            continue

if prev_id:
    try:
        client.exec_command(f"rm -rf {base_path}/{prev_id}")
    except:
        pass


client.close()
sftp_client.close()

R version 4.0.5 (2021-03-31) -- "Shake and Throw"
Copyright (C) 2021 The R Foundation for Statistical Computing
Platform: x86_64-pc-linux-gnu (64-bit)

R is free software and comes with ABSOLUTELY NO WARRANTY.
You are welcome to redistribute it under the terms of the
GNU General Public License versions 2 or 3.
For more information about these matters see
https://www.gnu.org/licenses/.




Processing 6SHZ...
Starting phenix.pdbtools
on Mon Apr 15 17:47:23 2024 by yliy0004

Processing files:
-------------------------------------------------------------------------------

  Found model, 6SHZ.pdb

Processing PHIL parameters:
-------------------------------------------------------------------------------

  Adding command-line PHIL:
  -------------------------
    keep=Chain B

Final processed PHIL parameters:
-------------------------------------------------------------------------------
  data_manager {
    model {
      file = "6SHZ.pdb"
    }
    default_model = "6SHZ.pdb"
  }
  modify 

In [9]:
client.close()
sftp_client.close()

In [ ]:
cgc_data.to_csv('Census_all_with_pdb.csv', index=False)

In [7]:
cgc_data = pd.read_csv('Census_all_with_pdb.csv')

# number of structures analysis

In [212]:
import plotly.express as px
fig = px.histogram(cgc_data, x="n_structures")
fig.show()

In [213]:
# horizontal boxplot
fig = px.box(cgc_data, x="n_structures", orientation='h')
fig.show()

# TCGA data

# TP53

In [38]:
gene = "TP53"

# read tp53 TCGA data
missense_data = pd.read_csv(f'{gene}_frequent-mutations.2024-04-15.tsv', sep='\t')

missense_data = missense_data[missense_data['consequence']=="Missense"].reset_index(drop=True)
missense_data['res_num'] = missense_data['protein_change'].apply(lambda x: x.split(' ')[1]).str.extract('(\d+)').astype(int) # get residue number

# sum the number of mutations for each residue
missense_data = missense_data.groupby('res_num').agg({'num_ssm_affected_cases': 'sum'}).reset_index()

# plot frequency vs score and save all plots to file
for pdb_id in top_structures[gene]:
    chains = get_chains_pdb_id(pdb_id)
    for chain in chains:
        # print(f"Processing {pdb_id} with chain {chain}...")
        # read FinalSum file
        try:
            with open(f"sbna_results/{pdb_id}/{chain}/{pdb_id}_monomer/FinalSum", "r") as f:
                final_sum = f.readlines()
        except Exception as e:
            print(f"Failed to read FinalSum for {pdb_id} with error {e}")
            continue
        # each line is like "MET1	-2.29160741999415", convert to table
        final_sum = [i.split() for i in final_sum]
        final_sum = [(i[0][:3], i[0][3:], i[1]) for i in final_sum]
        final_sum = pd.DataFrame(final_sum, columns=['res', 'num', 'score'])
        final_sum['num'] = final_sum['num'].astype(int)
        final_sum['score'] = final_sum['score'].astype(float)
        
        # join with missense_data
        # merge and if no values then 0
        final_sum = final_sum.merge(missense_data, how='left', left_on='num', right_on='res_num').fillna(0) 

        # plot frequency vs score and save all plots to file

        fig = px.scatter(final_sum, x='score', y='num_ssm_affected_cases', hover_data=['num'], 
                         labels={'num_ssm_affected_cases': 'Number of affected cases',
                                 'score': 'Network Score',
                                 'num': 'Residue Number'})
        
        fig.update_layout(title=f"TP53 Gene | PDB {pdb_id} | Chain {chain}")
        fig.update_xaxes(title_text='Network Score')
        fig.update_yaxes(title_text='Number of affected cases')

        # add label residue number to each point by hovering
        fig.update_traces(text=final_sum['num'], hoverinfo='text+y')



        # fig.write_image(f"plots/TP53_{pdb_id}_{chain}.png")
        fig.show()

Failed to read FinalSum for 3LW1 with error [Errno 2] No such file or directory: 'sbna_results/3LW1/P/3LW1_monomer/FinalSum'


# HRAS

In [11]:
gene = "HRAS"

# read tp53 TCGA data
missense_data = pd.read_csv(f'{gene}_frequent-mutations.2024-04-16.tsv', sep='\t')

missense_data = missense_data[missense_data['consequence']=="Missense"].reset_index(drop=True)
missense_data['res_num'] = missense_data['protein_change'].apply(lambda x: x.split(' ')[1]).str.extract('(\d+)').astype(int) # get residue number

# sum the number of mutations for each residue
missense_data = missense_data.groupby('res_num').agg({'num_ssm_affected_cases': 'sum'}).reset_index()

# plot frequency vs score and save all plots to file
for pdb_id in top_structures[gene]:
    chains = get_chains_pdb_id(pdb_id)
    for chain in chains:
        # print(f"Processing {pdb_id} with chain {chain}...")
        # read FinalSum file
        try:
            with open(f"sbna_results/{pdb_id}/{chain}/{pdb_id}_monomer/FinalSum", "r") as f:
                final_sum = f.readlines()
        except Exception as e:
            print(f"Failed to read FinalSum for {pdb_id} with error {e}")
            continue
        # each line is like "MET1	-2.29160741999415", convert to table
        final_sum = [i.split() for i in final_sum]
        final_sum = [(i[0][:3], i[0][3:], i[1]) for i in final_sum]
        final_sum = pd.DataFrame(final_sum, columns=['res', 'num', 'score'])
        final_sum['num'] = final_sum['num'].astype(int)
        final_sum['score'] = final_sum['score'].astype(float)
        
        # join with missense_data
        # merge and if no values then 0
        final_sum = final_sum.merge(missense_data, how='left', left_on='num', right_on='res_num').fillna(0) 

        # plot frequency vs score and save all plots to file

        fig = px.scatter(final_sum, x='score', y='num_ssm_affected_cases', hover_data=['num'], 
                         labels={'num_ssm_affected_cases': 'Number of affected cases',
                                 'score': 'Network Score',
                                 'num': 'Residue Number'})
        
        fig.update_layout(title=f"{gene} Gene | PDB {pdb_id} | Chain {chain}")
        fig.update_xaxes(title_text='Network Score')
        fig.update_yaxes(title_text='Number of affected cases')

        # add label residue number to each point by hovering
        fig.update_traces(text=final_sum['num'], hoverinfo='text+y')
        # fig.write_image(f"plots/{gene}/{gene}_{pdb_id}_{chain}.png")
        fig.show()

# EGFR

In [7]:
gene = "EGFR"

# read tp53 TCGA data
missense_data = pd.read_csv(f'{gene}_frequent-mutations.2024-04-16.tsv', sep='\t')

missense_data = missense_data[missense_data['consequence']=="Missense"].reset_index(drop=True)
missense_data['res_num'] = missense_data['protein_change'].apply(lambda x: x.split(' ')[1]).str.extract('(\d+)').astype(int) # get residue number

# sum the number of mutations for each residue
missense_data = missense_data.groupby('res_num').agg({'num_ssm_affected_cases': 'sum'}).reset_index()

# plot frequency vs score and save all plots to file
for pdb_id in top_structures[gene]:
    chains = get_chains_pdb_id(pdb_id)
    for chain in chains:
        # print(f"Processing {pdb_id} with chain {chain}...")
        # read FinalSum file
        try:
            with open(f"sbna_results/{pdb_id}/{chain}/{pdb_id}_monomer/FinalSum", "r") as f:
                final_sum = f.readlines()
        except Exception as e:
            print(f"Failed to read FinalSum for {pdb_id} with error {e}")
            continue
        # each line is like "MET1	-2.29160741999415", convert to table
        final_sum = [i.split() for i in final_sum]
        final_sum = [(i[0][:3], i[0][3:], i[1]) for i in final_sum]
        final_sum = pd.DataFrame(final_sum, columns=['res', 'num', 'score'])
        final_sum['num'] = final_sum['num'].astype(int)
        final_sum['score'] = final_sum['score'].astype(float)
        
        # join with missense_data
        # merge and if no values then 0
        final_sum = final_sum.merge(missense_data, how='left', left_on='num', right_on='res_num').fillna(0) 

        # plot frequency vs score and save all plots to file

        fig = px.scatter(final_sum, x='score', y='num_ssm_affected_cases', hover_data=['num'], 
                         labels={'num_ssm_affected_cases': 'Number of affected cases',
                                 'score': 'Network Score',
                                 'num': 'Residue Number'})
        
        fig.update_layout(title=f"{gene} Gene | PDB {pdb_id} | Chain {chain}")
        fig.update_xaxes(title_text='Network Score')
        fig.update_yaxes(title_text='Number of affected cases')

        # add label residue number to each point by hovering
        fig.update_traces(text=final_sum['num'], hoverinfo='text+y')

        # save image
        # fig.write_image(f"plots/{gene}/{gene}_{pdb_id}_{chain}.png")
        fig.show()

ValueError: could not convert string to float: 'NA'

# KRAS

In [13]:
gene = "KRAS"

# read tp53 TCGA data
missense_data = pd.read_csv(f'{gene}_frequent-mutations.2024-04-16.tsv', sep='\t')

missense_data = missense_data[missense_data['consequence']=="Missense"].reset_index(drop=True)
missense_data['res_num'] = missense_data['protein_change'].apply(lambda x: x.split(' ')[1]).str.extract('(\d+)').astype(int) # get residue number

# sum the number of mutations for each residue
missense_data = missense_data.groupby('res_num').agg({'num_ssm_affected_cases': 'sum'}).reset_index()

# plot frequency vs score and save all plots to file
for pdb_id in top_structures[gene]:
    chains = get_chains_pdb_id(pdb_id)
    for chain in chains:
        # print(f"Processing {pdb_id} with chain {chain}...")
        # read FinalSum file
        try:
            with open(f"sbna_results/{pdb_id}/{chain}/{pdb_id}_monomer/FinalSum", "r") as f:
                final_sum = f.readlines()
        except Exception as e:
            print(f"Failed to read FinalSum for {pdb_id} with error {e}")
            continue
        # each line is like "MET1	-2.29160741999415", convert to table
        final_sum = [i.split() for i in final_sum]
        final_sum = [(i[0][:3], i[0][3:], i[1]) for i in final_sum]
        final_sum = pd.DataFrame(final_sum, columns=['res', 'num', 'score'])
        final_sum['num'] = final_sum['num'].astype(int)
        final_sum['score'] = final_sum['score'].astype(float)
        
        # join with missense_data
        # merge and if no values then 0
        final_sum = final_sum.merge(missense_data, how='left', left_on='num', right_on='res_num').fillna(0) 

        # plot frequency vs score and save all plots to file

        fig = px.scatter(final_sum, x='score', y='num_ssm_affected_cases', hover_data=['num'], 
                         labels={'num_ssm_affected_cases': 'Number of affected cases',
                                 'score': 'Network Score',
                                 'num': 'Residue Number'})
        
        fig.update_layout(title=f"{gene} Gene | PDB {pdb_id} | Chain {chain}")
        fig.update_xaxes(title_text='Network Score')
        fig.update_yaxes(title_text='Number of affected cases')

        # add label residue number to each point by hovering
        fig.update_traces(text=final_sum['num'], hoverinfo='text+y')
        # fig.write_image(f"plots/{gene}/{gene}_{pdb_id}_{chain}.png")
        fig.show()

Failed to read FinalSum for 6P0Z with error [Errno 2] No such file or directory: 'sbna_results/6P0Z/B/6P0Z_monomer/FinalSum'
